In [1]:
!pip install mesa
# La clase `Model` se hace cargo de los atributos a nivel del modelo, maneja los agentes. 
# Cada modelo puede contener múltiples agentes y todos ellos son instancias de la clase `Agent`.
from mesa import Agent, Model 

# Debido a que necesitamos un solo agente por celda elegimos `SingleGrid` que fuerza un solo objeto por celda.
from mesa.space import MultiGrid

# Con `SimultaneousActivation` hacemos que todos los agentes se activen de manera simultanea.
from mesa.time import SimultaneousActivation

# Vamos a hacer uso de `DataCollector` para obtener el grid completo cada paso (o generación) y lo usaremos para graficarlo.
from mesa.datacollection import DataCollector

# mathplotlib lo usamos para graficar/visualizar como evoluciona el autómata celular.
%matplotlib inline
import matplotlib
import matplotlib.pyplot as plt
import matplotlib.animation as animation
plt.rcParams["animation.html"] = "jshtml"
matplotlib.rcParams['animation.embed_limit'] = 2**128

# Definimos los siguientes paquetes para manejar valores númericos.
import numpy as np
import pandas as pd

# Definimos otros paquetes que vamos a usar para medir el tiempo de ejecución de nuestro algoritmo.
import time
import datetime

import random

     |████████████████████████████████| 668 kB 7.6 MB/s 
     |████████████████████████████████| 63 kB 1.4 MB/s 


In [7]:
def get_grid(model):
  grid = np.zeros((model.grid.width, model.grid.height))
  for cell in model.grid.coord_iter():     
    cell_content, x, y = cell
    for obj in cell_content:
      if isinstance(obj, robotLimpieza):
        grid[x][y] = 2
      elif isinstance(obj, celda):
        grid[x][y] = obj.estado
  return grid

class robotLimpieza(Agent):
  def __init__(self, unique_id, model):
    super().__init__(unique_id, model)
    self.sig_pos = None 
  
  def step(self):
    #maquina de estados  
    vecinos =  self.model.grid.get_neighbors(
      self.pos,
      moore=True,
      include_center=True)
    for vecino in vecinos:
      if isinstance(vecino, celda) and self.pos == vecino.pos:
        if vecino.estado == 1:
          #limpiar
          vecino.sig_estado = 0
          self.sig_pos = self.pos
        else:
          vecinos2 = self.model.grid.get_neighborhood(
            self.pos,
            moore=True,
            include_center=False)
          vecino.sig_estado = 0
          self.sig_pos = self.random.choice(vecinos2)
        break
  def advance(self):
    vecinos =  self.model.grid.get_neighbors(
      self.pos,
      moore=True,
      include_center=True)
    for vecino in vecinos:
      if isinstance(vecino, celda) and self.pos == vecino.pos:
        vecino.estado = vecino.sig_estado
    self.model.grid.move_agent(self, self.sig_pos)

class celda(Agent): 
  #1 -> sucio
  #0 -> limpio
  def __init__(self, unique_id,model, estado):
    super().__init__(unique_id, model)
    self.pos = unique_id
    self.estado = estado 
    self.sig_estado = None

class Habitacion(Model):
  def __init__(self, M, N, num_agentes, porcent_celdas):
    self.num_agentes = num_agentes
    self.porcent_celdas_sucias = porcent_celdas
    self.porcent_celdas_limpias = 1 - porcent_celdas
    self.grid = MultiGrid(M, N, False)
    self.schedule = SimultaneousActivation(self)
        
    #Se llena el grid

    num_celdas_sucias = int(M * N * porcent_celdas)
    for (content, x, y) in self.grid.coord_iter():
      #podría hacerse un random de el número de celdas sucias 
      num = random.randint(0, 1) 
      if(num == 1 and num_celdas_sucias > 0):
        a = celda((x, y), self, 1)
        num_celdas_sucias -= 1
      else:
        a = celda((x, y), self, 0)
      self.grid.place_agent(a, (x, y))
      self.schedule.add(a)
        
    for id in range(num_agentes):
      r = robotLimpieza(id, self)
      self.grid.place_agent(r, (1, 1))
      self.schedule.add(r)
        
    # Aquí definimos con colector para obtener el grid completo.
    self.datacollector = DataCollector(
        model_reporters={"Grid": get_grid})
  def step(self):
    
    '''
    En cada paso el colector tomará la información que se definió y almacenará el grid para luego graficarlo.
    '''
    self.datacollector.collect(self)
    self.schedule.step()

In [11]:
# Definimos el tamaño del Grid
M = 15
N = 10
num_agentes = 5
porcent_celdas = 0.6
time_exec = 0.5

# Registramos el tiempo de inicio y corremos el modelo
model = Habitacion(M, N, num_agentes, porcent_celdas)
start_time = time.time()
while((time.time() - start_time) < time_exec):
  model.step()


# Imprimimos el tiempo que le tomó correr al modelo.
print('Tiempo de ejecución:', str(datetime.timedelta(seconds=(time.time() - start_time))))

Tiempo de ejecución: 0:00:00.500516


In [12]:
all_grid = model.datacollector.get_model_vars_dataframe()

In [13]:
%%capture

fig, axs = plt.subplots(figsize=(7,7))
axs.set_xticks([])
axs.set_yticks([])
patch = plt.imshow(all_grid.iloc[0][0], cmap=plt.cm.binary)

def animate(i):
    patch.set_data(all_grid.iloc[i][0])
    
anim = animation.FuncAnimation(fig, animate, frames=len(all_grid))

In [14]:
anim